# Reducing the raw data to just 2023 data

In [69]:
import pandas as pd

import numpy as np
import yfinance as yf
#Imports
import pandas as pd
from sklearn.impute import SimpleImputer
from sklearn.preprocessing import RobustScaler
from sklearn.pipeline import make_pipeline
from sklearn.compose import make_column_selector
from sklearn.compose import make_column_transformer
from sklearn.model_selection import train_test_split

from datetime import datetime, timedelta
from sklearn.model_selection import cross_validate, cross_val_score
from sklearn.linear_model import LinearRegression
from sklearn.linear_model import Ridge, Lasso, LinearRegression
from sklearn.ensemble import RandomForestRegressor
from sklearn.metrics import mean_absolute_error, mean_squared_error, r2_score
from sklearn.decomposition import PCA
import matplotlib.pyplot as plt
from xgboost import XGBRegressor

In [57]:
y = pd.read_csv("../raw_data/raw_data_target.csv")
y = y.drop(columns=["Unnamed: 0"])
y = y.set_index("Ticker")
y

Ratio ticker sp500
Ticker                    
AAL               0.785045
AAOI              4.957467
AAON              0.974026
AAPL              0.860731
ABCB              1.232920
...                    ...
ZKIN              0.749892
ZLAB              0.487622
ZS                1.194828
ZUMZ              0.843950
true              0.962451

[1649 rows x 1 columns]

In [41]:
df = pd.read_csv("../raw_data/raw_data_FINAL_ALL.csv")
df

Ticker  2023 Ordinary Shares Number  2023 Share Issued  2023 Net Debt  \
0         A                  292123241.0        292123241.0   1.145000e+09   
1        AA                  178472464.0        178472464.0   8.670000e+08   
2      AACG                   64000260.0         64585618.0            NaN   
3      AACI                    8072849.0          8072849.0   2.504155e+06   
4     AACIW                    8072849.0          8072849.0   2.504155e+06   
...     ...                          ...                ...            ...   
6329   ZVIA                   54220017.0         54220017.0            NaN   
6330   ZVRA                          NaN                NaN            NaN   
6331   ZVSA                     405205.0           405211.0            NaN   
6332   ZYME                   70115997.0         70115997.0            NaN   
6333   ZYXI                   32933776.0         41478820.0   1.302600e+07   

      2023 Total Debt  2023 Tangible Book Value  2023 Invested Capital  \
0        2.735000e+09              1.410000e+09           8.580000e+09   
1        1.915000e+09              4.068000e+09           6.062000e+09   
2        2.260687e+07             -1.421377e+08           1.130379e+08   
3        2.564439e+06              1.683079e+07           1.939523e+07   
4        2.564439e+06              1.683079e+07           1.939523e+07   
...               ...                       ...                    ...   
6329     1.948000e+06              8.635500e+07           8.987800e+07   
6330              NaN                       NaN                    NaN   
6331     8.656000e+03             -7.573306e+06           1.107460e+07   
6332     2.672200e+07              4.275060e+08           4.648060e+08   
6333     7.616800e+07              1.757000e+07           1.037340e+08   

      2023 Working Capital  2023 Net Tangible Assets  \
0             2.583000e+09              1.410000e+09   
1             1.375000e+09              4.068000e+09   
2            -2.439576e+08             -1.421377e+08   
3            -8.493234e+06              1.683079e+07   
4            -8.493234e+06              1.683079e+07   
...                    ...                       ...   
6329          5.497000e+07              8.635500e+07   
6330                   NaN                       NaN   
6331         -6.841639e+06             -7.573305e+06   
6332          3.571630e+08              4.275060e+08   
6333          6.932300e+07              1.757000e+07   

      2023 Common Stock Equity  ...  2024 Interest Received Cfo  \
0                 5.845000e+09  ...                         NaN   
1                 4.251000e+09  ...                         NaN   
2                 1.130379e+08  ...                         NaN   
3                 1.683079e+07  ...                         NaN   
4                 1.683079e+07  ...                         NaN   
...                        ...  ...                         ...   
6329              8.987800e+07  ...                         NaN   
6330                       NaN  ...                         NaN   
6331              1.107460e+07  ...                         NaN   
6332              4.648060e+08  ...                         NaN   
6333              4.612900e+07  ...                         NaN   

      2023 Dividends Paid Direct  2022 Dividends Paid Direct  \
0                            NaN                         NaN   
1                            NaN                         NaN   
2                            NaN                         NaN   
3                            NaN                         NaN   
4                            NaN                         NaN   
...                          ...                         ...   
6329                         NaN                         NaN   
6330                         NaN                         NaN   
6331                         NaN                         NaN   
6332                         NaN                         NaN 

In [42]:
df_tickers = pd.DataFrame(df["Ticker"])
df_tickers

Ticker
0         A
1        AA
2      AACG
3      AACI
4     AACIW
...     ...
6329   ZVIA
6330   ZVRA
6331   ZVSA
6332   ZYME
6333   ZYXI

[6334 rows x 1 columns]

In [58]:
df_tickers.to_csv("raw_data_ticker_labels_ALL.csv")

In [43]:
df_2023 = df.filter(like="2023", axis=1).copy()
df_2023

2023 Ordinary Shares Number  2023 Share Issued  2023 Net Debt  \
0                     292123241.0        292123241.0   1.145000e+09   
1                     178472464.0        178472464.0   8.670000e+08   
2                      64000260.0         64585618.0            NaN   
3                       8072849.0          8072849.0   2.504155e+06   
4                       8072849.0          8072849.0   2.504155e+06   
...                           ...                ...            ...   
6329                   54220017.0         54220017.0            NaN   
6330                          NaN                NaN            NaN   
6331                     405205.0           405211.0            NaN   
6332                   70115997.0         70115997.0            NaN   
6333                   32933776.0         41478820.0   1.302600e+07   

      2023 Total Debt  2023 Tangible Book Value  2023 Invested Capital  \
0        2.735000e+09              1.410000e+09           8.580000e+09   
1        1.915000e+09              4.068000e+09           6.062000e+09   
2        2.260687e+07             -1.421377e+08           1.130379e+08   
3        2.564439e+06              1.683079e+07           1.939523e+07   
4        2.564439e+06              1.683079e+07           1.939523e+07   
...               ...                       ...                    ...   
6329     1.948000e+06              8.635500e+07           8.987800e+07   
6330              NaN                       NaN                    NaN   
6331     8.656000e+03             -7.573306e+06           1.107460e+07   
6332     2.672200e+07              4.275060e+08           4.648060e+08   
6333     7.616800e+07              1.757000e+07           1.037340e+08   

      2023 Working Capital  2023 Net Tangible Assets  \
0             2.583000e+09              1.410000e+09   
1             1.375000e+09              4.068000e+09   
2            -2.439576e+08             -1.421377e+08   
3            -8.493234e+06              1.683079e+07   
4            -8.493234e+06              1.683079e+07   
...                    ...                       ...   
6329          5.497000e+07              8.635500e+07   
6330                   NaN                       NaN   
6331         -6.841639e+06             -7.573305e+06   
6332          3.571630e+08              4.275060e+08   
6333          6.932300e+07              1.757000e+07   

      2023 Common Stock Equity  2023 Total Capitalization  ...  \
0                 5.845000e+09               8.580000e+09  ...   
1                 4.251000e+09               5.983000e+09  ...   
2                 1.130379e+08               1.130379e+08  ...   
3                 1.683079e+07               1.683079e+07  ...   
4                 1.683079e+07               1.683079e+07  ...   
...                        ...                        ...  ...   
6329              8.987800e+07               8.987800e+07  ...   
6330                       NaN                        NaN  ...   
6331              1.107460e+07               1.107460e+07  ...   
6332              4.648060e+08               4.648060e+08  ...   
6333              4.612900e+07               1.037340e+08  ...   

      2023 Receiptsfrom Government Grants  2023 Receiptsfrom Customers  \
0                                     NaN                          NaN   
1                                     NaN                          NaN   
2                                     NaN                          NaN   
3                                     NaN                          NaN   
4                                     NaN                          NaN   
...                                   ...                          ...   
6329                                  NaN                          NaN   
6330                                  NaN                          NaN   
6331                                  NaN                          NaN   
6332                                  NaN                 

In [44]:
df_2023 = df_2023.join( df_tickers, how="inner")
df_2023

2023 Ordinary Shares Number  2023 Share Issued  2023 Net Debt  \
0                     292123241.0        292123241.0   1.145000e+09   
1                     178472464.0        178472464.0   8.670000e+08   
2                      64000260.0         64585618.0            NaN   
3                       8072849.0          8072849.0   2.504155e+06   
4                       8072849.0          8072849.0   2.504155e+06   
...                           ...                ...            ...   
6329                   54220017.0         54220017.0            NaN   
6330                          NaN                NaN            NaN   
6331                     405205.0           405211.0            NaN   
6332                   70115997.0         70115997.0            NaN   
6333                   32933776.0         41478820.0   1.302600e+07   

      2023 Total Debt  2023 Tangible Book Value  2023 Invested Capital  \
0        2.735000e+09              1.410000e+09           8.580000e+09   
1        1.915000e+09              4.068000e+09           6.062000e+09   
2        2.260687e+07             -1.421377e+08           1.130379e+08   
3        2.564439e+06              1.683079e+07           1.939523e+07   
4        2.564439e+06              1.683079e+07           1.939523e+07   
...               ...                       ...                    ...   
6329     1.948000e+06              8.635500e+07           8.987800e+07   
6330              NaN                       NaN                    NaN   
6331     8.656000e+03             -7.573306e+06           1.107460e+07   
6332     2.672200e+07              4.275060e+08           4.648060e+08   
6333     7.616800e+07              1.757000e+07           1.037340e+08   

      2023 Working Capital  2023 Net Tangible Assets  \
0             2.583000e+09              1.410000e+09   
1             1.375000e+09              4.068000e+09   
2            -2.439576e+08             -1.421377e+08   
3            -8.493234e+06              1.683079e+07   
4            -8.493234e+06              1.683079e+07   
...                    ...                       ...   
6329          5.497000e+07              8.635500e+07   
6330                   NaN                       NaN   
6331         -6.841639e+06             -7.573305e+06   
6332          3.571630e+08              4.275060e+08   
6333          6.932300e+07              1.757000e+07   

      2023 Common Stock Equity  2023 Total Capitalization  ...  \
0                 5.845000e+09               8.580000e+09  ...   
1                 4.251000e+09               5.983000e+09  ...   
2                 1.130379e+08               1.130379e+08  ...   
3                 1.683079e+07               1.683079e+07  ...   
4                 1.683079e+07               1.683079e+07  ...   
...                        ...                        ...  ...   
6329              8.987800e+07               8.987800e+07  ...   
6330                       NaN                        NaN  ...   
6331              1.107460e+07               1.107460e+07  ...   
6332              4.648060e+08               4.648060e+08  ...   
6333              4.612900e+07               1.037340e+08  ...   

      2023 Receiptsfrom Customers  2023 Interest Received Direct  \
0                             NaN                            NaN   
1                             NaN                            NaN   
2                             NaN                            NaN   
3                             NaN                            NaN   
4                             NaN                            NaN   
...                           ...                            ...   
6329                          NaN                            NaN   
6330                          NaN                            NaN   
6331                          NaN                            NaN   
6332                          NaN                            NaN   
6333                          NaN                 

## Clean the dataframe from 2023

In [45]:
#Imports
import pandas as pd
from sklearn.impute import SimpleImputer
from sklearn.preprocessing import RobustScaler
from sklearn.pipeline import make_pipeline
from sklearn.compose import make_column_selector
from sklearn.compose import make_column_transformer

#CLEANING THE DATA:

#drop columns that have more than 30% of missing data:
def remove_shitty_columns(df):
    for column in df.columns:
        if df[column].isnull().sum()/len(df) > 0.3:
            df.drop(columns=[column], inplace=True)
    return df


#drop rows that have more than 30% of missing values
def remove_shitty_rows(df):
    threshold = 0.3 * df.shape[1]  # Calculate the threshold for missing values
    df = df.dropna(thresh=int(df.shape[1] - threshold))
    return df

#FINAL CLEANING FUNCTION
def clean_dataframe(df):
    df = remove_shitty_columns(df)
    df = remove_shitty_rows(df)
    df = df.reset_index(drop=True)
    return df


#PREPROCESSING
def preprocessing_the_data(df):
    #use simple impute with strategy = "constant"
    imputer = SimpleImputer(strategy="constant", fill_value=0)

    #Robust Scaler to Scale data because of outliers
    rb_scaler = RobustScaler()

    #select numerical columns
    num_transformer = make_pipeline(imputer, rb_scaler)
    num_columns = make_column_selector(dtype_exclude="object")

    #Create Preproc Pipeline
    preproc_basic = make_column_transformer((num_transformer, num_columns))

    #Apply Preprocessing to dataframe
    preprocessed_data = preproc_basic.fit_transform(df)

    #Change column names of transformed dataframe
    df_preproc = pd.DataFrame(preprocessed_data, columns=preproc_basic.get_feature_names_out())

    #Merge with tickers
    df_preproc = df_preproc.join(df.Ticker)

    return df_preproc


"""to import in the other file:

from preprocessing import clean_dataframe, preprocessing_the_data

df = clean_dataframe(df)
df = propcessing_the_data(df)

"""


'to import in the other file:\n\nfrom preprocessing import clean_dataframe, preprocessing_the_data\n\ndf = clean_dataframe(df)\ndf = propcessing_the_data(df)\n\n'

In [46]:
df_2023 = clean_dataframe(df_2023)
df_2023 = preprocessing_the_data(df_2023)


In [47]:
df_2023

pipeline__2023 Ordinary Shares Number  pipeline__2023 Share Issued  \
0                                  1.820402                     1.660844   
1                                  0.957890                     0.863273   
2                                  0.089144                     0.064045   
3                                 -0.335297                    -0.332547   
4                                 -0.335297                    -0.332547   
...                                     ...                          ...   
5627                               0.631804                     0.561739   
5628                               0.014921                    -0.008698   
5629                              -0.393488                    -0.386356   
5630                               0.135558                     0.102856   
5631                              -0.146624                    -0.098112   

      pipeline__2023 Total Debt  pipeline__2023 Tangible Book Value  \
0                      1.708296                            2.107820   
1                      1.167091                            6.363139   
2                     -0.081900                           -0.377072   
3                     -0.095128                           -0.122571   
4                     -0.095128                           -0.122571   
...                         ...                                 ...   
5627                   0.073175                           -0.101539   
5628                  -0.095535                           -0.011267   
5629                  -0.096815                           -0.161641   
5630                  -0.079184                            0.534898   
5631                  -0.046550                           -0.121388   

      pipeline__2023 Invested Capital  pipeline__2023 Working Capital  \
0                            2.638558                        8.356595   
1                            1.813790                        4.388426   
2                           -0.134787                       -0.929702   
3                           -0.165460                       -0.156223   
4                           -0.165460                       -0.156223   
...                               ...                             ...   
5627                        -0.071071                        0.551433   
5628                        -0.142373                        0.052248   
5629                        -0.168185                       -0.150797   
5630                        -0.019566                        1.044924   
5631                        -0.137835                        0.099396   

      pipeline__2023 Net Tangible Assets  pipeline__2023 Common Stock Equity  \
0                               2.127603                            3.597811   
1                               6.415388                            2.564874   
2                              -0.376247                           -0.116590   
3                              -0.119805                           -0.178934   
4                              -0.119805                           -0.178934   
...                                  ...                                 ...   
5627                           -0.098613                           -0.126879   
5628                           -0.007651                           -0.131598   
5629                           -0.159173                           -0.182664   
5630                            0.542681                            0.111361   
5631                           -0.118613                           -0.159948   

      pipeline__2023 Total Capitalization  \
0                                2.728212   
1                                1.850950   
2                               -0.131913   
3                               -0.164412   
4                               -0.164412   
...                                   ...   
5627                            -0.066203   
5628                            -0.139736 

In [48]:
pd.set_option('display.max_columns', None)

In [49]:
df_2023

pipeline__2023 Ordinary Shares Number  pipeline__2023 Share Issued  \
0                                  1.820402                     1.660844   
1                                  0.957890                     0.863273   
2                                  0.089144                     0.064045   
3                                 -0.335297                    -0.332547   
4                                 -0.335297                    -0.332547   
...                                     ...                          ...   
5627                               0.631804                     0.561739   
5628                               0.014921                    -0.008698   
5629                              -0.393488                    -0.386356   
5630                               0.135558                     0.102856   
5631                              -0.146624                    -0.098112   

      pipeline__2023 Total Debt  pipeline__2023 Tangible Book Value  \
0                      1.708296                            2.107820   
1                      1.167091                            6.363139   
2                     -0.081900                           -0.377072   
3                     -0.095128                           -0.122571   
4                     -0.095128                           -0.122571   
...                         ...                                 ...   
5627                   0.073175                           -0.101539   
5628                  -0.095535                           -0.011267   
5629                  -0.096815                           -0.161641   
5630                  -0.079184                            0.534898   
5631                  -0.046550                           -0.121388   

      pipeline__2023 Invested Capital  pipeline__2023 Working Capital  \
0                            2.638558                        8.356595   
1                            1.813790                        4.388426   
2                           -0.134787                       -0.929702   
3                           -0.165460                       -0.156223   
4                           -0.165460                       -0.156223   
...                               ...                             ...   
5627                        -0.071071                        0.551433   
5628                        -0.142373                        0.052248   
5629                        -0.168185                       -0.150797   
5630                        -0.019566                        1.044924   
5631                        -0.137835                        0.099396   

      pipeline__2023 Net Tangible Assets  pipeline__2023 Common Stock Equity  \
0                               2.127603                            3.597811   
1                               6.415388                            2.564874   
2                              -0.376247                           -0.116590   
3                              -0.119805                           -0.178934   
4                              -0.119805                           -0.178934   
...                                  ...                                 ...   
5627                           -0.098613                           -0.126879   
5628                           -0.007651                           -0.131598   
5629                           -0.159173                           -0.182664   
5630                            0.542681                            0.111361   
5631                           -0.118613                           -0.159948   

      pipeline__2023 Total Capitalization  \
0                                2.728212   
1                                1.850950   
2                               -0.131913   
3                               -0.164412   
4                               -0.164412   
...                                   ...   
5627                            -0.066203   
5628                            -0.139736 

## ML model with ratios with Gradient Boosting: 

In [60]:
df_small = pd.read_csv("../raw_data/Raw_data_number_one.csv")
df_small

Ticker  2023 Treasury Shares Number  2023 Ordinary Shares Number  \
0       AAL                          0.0                 6.542732e+08   
1      AAME                          NaN                          NaN   
2      AAOI                          NaN                 3.814800e+07   
3      AAON                          NaN                 8.150838e+07   
4      AAPL                          0.0                 1.555006e+10   
...     ...                          ...                          ...   
1763   ZKIN                          NaN                          NaN   
1764   ZLAB                    4912200.0                 9.722391e+08   
1765     ZS                          NaN                 1.471690e+08   
1766   ZUMZ                          NaN                 1.948900e+07   
1767   true                          NaN                 9.109154e+07   

      2023 Share Issued  2023 Net Debt  2023 Total Debt  \
0          6.542732e+08   3.232400e+10     4.066300e+10   
1                   NaN            NaN              NaN   
2          3.814800e+07   6.983200e+07     1.210730e+08   
3          8.150838e+07   3.804100e+07     5.055000e+07   
4          1.555006e+10   8.112300e+10     1.110880e+11   
...                 ...            ...              ...   
1763                NaN            NaN              NaN   
1764       9.771513e+08            NaN     1.515100e+07   
1765       1.471690e+08            NaN     1.210545e+09   
1766       1.948900e+07            NaN     2.542950e+08   
1767       9.109154e+07            NaN     1.440900e+07   

      2023 Tangible Book Value  2023 Invested Capital  2023 Working Capital  \
0                -1.134400e+10           2.770000e+10         -8.490000e+09   
1                          NaN                    NaN                   NaN   
2                 2.062110e+08           3.300670e+08          7.924700e+07   
3                 5.852790e+08           7.735520e+08          2.822050e+08   
4                 6.214600e+10           1.732340e+11         -1.742000e+09   
...                        ...                    ...                   ...   
1763                       NaN                    NaN                   NaN   
1764              7.796600e+08           7.961180e+08          7.365390e+08   
1765              6.100610e+08           1.859271e+09          1.354446e+09   
1766              3.363190e+08           4.073280e+08          1.943690e+08   
1767              1.518400e+08           1.602150e+08          1.341040e+08   

      2023 Net Tangible Assets  2023 Capital Lease Obligations  \
0                -1.134400e+10                    7.761000e+09   
1                          NaN                             NaN   
2                 2.062110e+08                    5.875000e+06   
3                 5.852790e+08                    1.222200e+07   
4                 6.214600e+10                             NaN   
...                        ...                             ...   
1763                       NaN                             NaN   
1764              7.796600e+08                    1.515100e+07   
1765              6.100610e+08                    7.638600e+07   
1766              3.363190e+08                    2.542950e+08   
1767              1.518400e+08                    1.440900e+07   

      2023 Common Stock Equity  2023 Total Capitalization  \
0                -5.202000e+09               2.406800e+10   
1                          NaN                        NaN   
2                 2.148690e+08               2.911020e+08   
3                 7.352240e+08               7.735520e+08   
4                 6.214600e+10               1.574270e+11   
...                        ...                        ...   
1763                       NaN                        NaN   
1764              7.961180e+08               7.961180e+08   
1765              7.251120e+08               1.859271e+09   
1766              4.073280e+08               4.073280e+08   
1767  

In [61]:
df_small_clean = clean_dataframe(df_small)
df_small_clean = preprocessing_the_data(df_small_clean)
df_small_clean

pipeline__2023 Ordinary Shares Number  pipeline__2023 Share Issued  \
0                                  8.004987                     7.515304   
1                                  0.018042                    -0.022246   
2                                  0.580131                     0.508216   
3                                201.101827                   189.747335   
4                                  0.418674                     0.398206   
...                                     ...                          ...   
1644                              -0.476477                    -0.488941   
1645                              12.126837                    11.465329   
1646                               1.431302                     1.311495   
1647                              -0.223838                    -0.250516   
1648                               0.704359                     0.625455   

      pipeline__2023 Total Debt  pipeline__2023 Tangible Book Value  \
0                     55.734768                          -23.148653   
1                     -0.007525                            0.157374   
2                     -0.104489                            0.922258   
3                    152.564180                          125.139545   
4                      0.705827                            4.428940   
...                         ...                                 ...   
1644                  -0.173992                           -0.258718   
1645                  -0.153160                            1.314480   
1646                   1.490422                            0.972263   
1647                   0.175646                            0.419906   
1648                  -0.154180                            0.047664   

      pipeline__2023 Invested Capital  pipeline__2023 Working Capital  \
0                           15.145524                      -27.907990   
1                           -0.075072                        0.088309   
2                            0.171553                        0.751386   
3                           96.077914                       -5.861826   
4                            2.002865                       -0.170596   
...                               ...                             ...   
1644                        -0.258624                       -0.170596   
1645                         0.184102                        2.235725   
1646                         0.775329                        4.254469   
1647                        -0.032106                        0.464420   
1648                        -0.169527                        0.267530   

      pipeline__2023 Net Tangible Assets  \
0                             -23.064565   
1                               0.156803   
2                               0.918908   
3                             124.684969   
4                               4.412852   
...                                  ...   
1644                           -0.257779   
1645                            1.309705   
1646                            0.968732   
1647                            0.418381   
1648                            0.047491   

      pipeline__2023 Capital Lease Obligations  \
0                                   139.337965   
1                                    -0.045400   
2                                     0.068675   
3                                    -0.150992   
4                                    -0.150992   
...                                        ...   
1644                                 -0.150992   
1645                                  0.121318   
1646                                  1.221899   
1647                                  4.419469   
1648                                  0.107982   

      pipeline__2023 Common Stock Equity  pipeline__2023 Total Capitalization  \
0                              -5.430906                            13.420363   
1                              -0.056036                            -0.

In [79]:
X_small_reduced = df_small_clean[[ "pipeline__2023 Ratio ticker sp500", 
                         "pipeline__2022 Ratio ticker sp500", 
                         "pipeline__2021 Ratio ticker sp500",
                        "pipeline__2020 Ratio ticker sp500", "Ticker"]]

In [80]:
X_small_reduced

pipeline__2023 Ratio ticker sp500  pipeline__2022 Ratio ticker sp500  \
0                              0.110173                          -0.090977   
1                             17.045832                          -0.781155   
2                              0.937091                           0.512387   
3                              0.587249                           0.474382   
4                              0.279406                           0.407539   
...                                 ...                                ...   
1644                          -1.900304                          -0.962432   
1645                          -0.289921                          -0.519939   
1646                           0.316123                          -0.377801   
1647                          -0.408094                          -0.032692   
1648                           0.532747                           0.024220   

      pipeline__2021 Ratio ticker sp500  pipeline__2020 Ratio ticker sp500  \
0                             -0.006855                          -0.747803   
1                             -0.905159                          -0.533057   
2                              0.063391                           0.508978   
3                              0.061296                           1.720461   
4                              0.190881                          -0.168701   
...                                 ...                                ...   
1644                           1.593082                           0.020274   
1645                          -1.058512                           3.386363   
1646                           0.826357                           0.922797   
1647                           0.374460                           0.281814   
1648                          -0.608170                          -0.251870   

     Ticker  
0       AAL  
1      AAOI  
2      AAON  
3      AAPL  
4      ABCB  
...     ...  
1644   ZKIN  
1645   ZLAB  
1646     ZS  
1647   ZUMZ  
1648   true  

[1649 rows x 5 columns]

In [66]:
y.rename(columns={"Ratio ticker sp500": "2024 Ratio ticker sp500"}, inplace=True)

In [67]:
y

2024 Ratio ticker sp500
Ticker                         
AAL                    0.785045
AAOI                   4.957467
AAON                   0.974026
AAPL                   0.860731
ABCB                   1.232920
...                         ...
ZKIN                   0.749892
ZLAB                   0.487622
ZS                     1.194828
ZUMZ                   0.843950
true                   0.962451

[1649 rows x 1 columns]

In [75]:
y.isna().sum()

2024 Ratio ticker sp500    17
dtype: int64

In [77]:
y = y.dropna()
y

2024 Ratio ticker sp500
Ticker                         
AAL                    0.785045
AAOI                   4.957467
AAON                   0.974026
AAPL                   0.860731
ABCB                   1.232920
...                         ...
ZKIN                   0.749892
ZLAB                   0.487622
ZS                     1.194828
ZUMZ                   0.843950
true                   0.962451

[1632 rows x 1 columns]

In [82]:
X_small_reduced.set_index("Ticker", inplace=True)

In [83]:
X_small_reduced

pipeline__2023 Ratio ticker sp500  pipeline__2022 Ratio ticker sp500  \
Ticker                                                                         
AAL                              0.110173                          -0.090977   
AAOI                            17.045832                          -0.781155   
AAON                             0.937091                           0.512387   
AAPL                             0.587249                           0.474382   
ABCB                             0.279406                           0.407539   
...                                   ...                                ...   
ZKIN                            -1.900304                          -0.962432   
ZLAB                            -0.289921                          -0.519939   
ZS                               0.316123                          -0.377801   
ZUMZ                            -0.408094                          -0.032692   
true                             0.532747                           0.024220   

        pipeline__2021 Ratio ticker sp500  pipeline__2020 Ratio ticker sp500  
Ticker                                                                        
AAL                             -0.006855                          -0.747803  
AAOI                            -0.905159                          -0.533057  
AAON                             0.063391                           0.508978  
AAPL                             0.061296                           1.720461  
ABCB                             0.190881                          -0.168701  
...                                   ...                                ...  
ZKIN                             1.593082                           0.020274  
ZLAB                            -1.058512                           3.386363  
ZS                               0.826357                           0.922797  
ZUMZ                             0.374460                           0.281814  
true                            -0.608170                          -0.251870  

[1649 rows x 4 columns]

In [84]:
df_small = X_small_reduced.join(y, how="right")
df_small

pipeline__2023 Ratio ticker sp500  pipeline__2022 Ratio ticker sp500  \
Ticker                                                                         
AAL                              0.110173                          -0.090977   
AAOI                            17.045832                          -0.781155   
AAON                             0.937091                           0.512387   
AAPL                             0.587249                           0.474382   
ABCB                             0.279406                           0.407539   
...                                   ...                                ...   
ZKIN                            -1.900304                          -0.962432   
ZLAB                            -0.289921                          -0.519939   
ZS                               0.316123                          -0.377801   
ZUMZ                            -0.408094                          -0.032692   
true                             0.532747                           0.024220   

        pipeline__2021 Ratio ticker sp500  pipeline__2020 Ratio ticker sp500  \
Ticker                                                                         
AAL                             -0.006855                          -0.747803   
AAOI                            -0.905159                          -0.533057   
AAON                             0.063391                           0.508978   
AAPL                             0.061296                           1.720461   
ABCB                             0.190881                          -0.168701   
...                                   ...                                ...   
ZKIN                             1.593082                           0.020274   
ZLAB                            -1.058512                           3.386363   
ZS                               0.826357                           0.922797   
ZUMZ                             0.374460                           0.281814   
true                            -0.608170                          -0.251870   

        2024 Ratio ticker sp500  
Ticker                           
AAL                    0.785045  
AAOI                   4.957467  
AAON                   0.974026  
AAPL                   0.860731  
ABCB                   1.232920  
...                         ...  
ZKIN                   0.749892  
ZLAB                   0.487622  
ZS                     1.194828  
ZUMZ                   0.843950  
true                   0.962451  

[1632 rows x 5 columns]

In [85]:
X_small_reduced = df_small.drop(columns=["2024 Ratio ticker sp500"])
y = df_small["2024 Ratio ticker sp500"]

In [86]:
X_small_reduced

pipeline__2023 Ratio ticker sp500  pipeline__2022 Ratio ticker sp500  \
Ticker                                                                         
AAL                              0.110173                          -0.090977   
AAOI                            17.045832                          -0.781155   
AAON                             0.937091                           0.512387   
AAPL                             0.587249                           0.474382   
ABCB                             0.279406                           0.407539   
...                                   ...                                ...   
ZKIN                            -1.900304                          -0.962432   
ZLAB                            -0.289921                          -0.519939   
ZS                               0.316123                          -0.377801   
ZUMZ                            -0.408094                          -0.032692   
true                             0.532747                           0.024220   

        pipeline__2021 Ratio ticker sp500  pipeline__2020 Ratio ticker sp500  
Ticker                                                                        
AAL                             -0.006855                          -0.747803  
AAOI                            -0.905159                          -0.533057  
AAON                             0.063391                           0.508978  
AAPL                             0.061296                           1.720461  
ABCB                             0.190881                          -0.168701  
...                                   ...                                ...  
ZKIN                             1.593082                           0.020274  
ZLAB                            -1.058512                           3.386363  
ZS                               0.826357                           0.922797  
ZUMZ                             0.374460                           0.281814  
true                            -0.608170                          -0.251870  

[1632 rows x 4 columns]

In [87]:
y

Ticker
AAL     0.785045
AAOI    4.957467
AAON    0.974026
AAPL    0.860731
ABCB    1.232920
          ...   
ZKIN    0.749892
ZLAB    0.487622
ZS      1.194828
ZUMZ    0.843950
true    0.962451
Name: 2024 Ratio ticker sp500, Length: 1632, dtype: float64

In [88]:
X_train, X_test, y_train, y_test = train_test_split(X_small_reduced, y, test_size=0.3)

In [90]:
X_test, X_val, y_test, y_val = train_test_split(X_test, y_test, test_size = 0.5)

In [92]:
xgb_reg = XGBRegressor(max_depth=10, n_estimators=100, learning_rate=0.1)

xgb_reg.fit(X_train, y_train,
    # evaluate loss at each iteration
    eval_set=[(X_train, y_train), (X_val, y_val)],  
    # stop iterating when eval loss increases 5 times in a row
    early_stopping_rounds=5)


#y_pred = xgb_reg.predict(X_test)
 

#Or integrate it into scikit-learn as a Pipeline 🎉

#from sklearn.pipeline import make_pipeline

#pipe_xgb = make_pipeline(xgb_reg)
cv_results = cross_validate(xgb_reg, X_train, y_train, cv=10, scoring='r2')
cv_results

[0]	validation_0-rmse:0.57390	validation_1-rmse:0.65636
[1]	validation_0-rmse:0.54179	validation_1-rmse:0.64263
[2]	validation_0-rmse:0.51235	validation_1-rmse:0.63212
[3]	validation_0-rmse:0.48478	validation_1-rmse:0.62500
[4]	validation_0-rmse:0.45950	validation_1-rmse:0.62304
[5]	validation_0-rmse:0.43574	validation_1-rmse:0.62210
[6]	validation_0-rmse:0.41371	validation_1-rmse:0.62481
[7]	validation_0-rmse:0.39297	validation_1-rmse:0.62809
[8]	validation_0-rmse:0.37372	validation_1-rmse:0.63312
[9]	validation_0-rmse:0.35628	validation_1-rmse:0.63998


/Users/manonantonacci/.pyenv/versions/3.10.6/envs/project_env/lib/python3.10/site-packages/xgboost/sklearn.py:889: UserWarning: `early_stopping_rounds` in `fit` method is deprecated for better compatibility with scikit-learn, use `early_stopping_rounds` in constructor or`set_params` instead.
  warnings.warn(


{'fit_time': array([0.12521338, 0.11319828, 0.10726476, 0.11029005, 0.15866303,
        0.15295815, 0.1550982 , 0.18887496, 0.13516068, 0.12975311]),
 'score_time': array([0.00278091, 0.00116301, 0.00135112, 0.00113583, 0.00120187,
        0.00130987, 0.00122881, 0.00195003, 0.00121236, 0.00130391]),
 'test_score': array([ 0.11420438, -1.67593189,  0.12252147,  0.30590951,  0.16374384,
        -0.75563665,  0.15791072,  0.04748291,  0.18951591,  0.04637873])}

# Try Gradient Boosting with just data from 2023

In [93]:
df_small = pd.read_csv("../raw_data/Raw_data_number_one.csv")
df_small

Ticker  2023 Treasury Shares Number  2023 Ordinary Shares Number  \
0       AAL                          0.0                 6.542732e+08   
1      AAME                          NaN                          NaN   
2      AAOI                          NaN                 3.814800e+07   
3      AAON                          NaN                 8.150838e+07   
4      AAPL                          0.0                 1.555006e+10   
...     ...                          ...                          ...   
1763   ZKIN                          NaN                          NaN   
1764   ZLAB                    4912200.0                 9.722391e+08   
1765     ZS                          NaN                 1.471690e+08   
1766   ZUMZ                          NaN                 1.948900e+07   
1767   true                          NaN                 9.109154e+07   

      2023 Share Issued  2023 Net Debt  2023 Total Debt  \
0          6.542732e+08   3.232400e+10     4.066300e+10   
1                   NaN            NaN              NaN   
2          3.814800e+07   6.983200e+07     1.210730e+08   
3          8.150838e+07   3.804100e+07     5.055000e+07   
4          1.555006e+10   8.112300e+10     1.110880e+11   
...                 ...            ...              ...   
1763                NaN            NaN              NaN   
1764       9.771513e+08            NaN     1.515100e+07   
1765       1.471690e+08            NaN     1.210545e+09   
1766       1.948900e+07            NaN     2.542950e+08   
1767       9.109154e+07            NaN     1.440900e+07   

      2023 Tangible Book Value  2023 Invested Capital  2023 Working Capital  \
0                -1.134400e+10           2.770000e+10         -8.490000e+09   
1                          NaN                    NaN                   NaN   
2                 2.062110e+08           3.300670e+08          7.924700e+07   
3                 5.852790e+08           7.735520e+08          2.822050e+08   
4                 6.214600e+10           1.732340e+11         -1.742000e+09   
...                        ...                    ...                   ...   
1763                       NaN                    NaN                   NaN   
1764              7.796600e+08           7.961180e+08          7.365390e+08   
1765              6.100610e+08           1.859271e+09          1.354446e+09   
1766              3.363190e+08           4.073280e+08          1.943690e+08   
1767              1.518400e+08           1.602150e+08          1.341040e+08   

      2023 Net Tangible Assets  2023 Capital Lease Obligations  \
0                -1.134400e+10                    7.761000e+09   
1                          NaN                             NaN   
2                 2.062110e+08                    5.875000e+06   
3                 5.852790e+08                    1.222200e+07   
4                 6.214600e+10                             NaN   
...                        ...                             ...   
1763                       NaN                             NaN   
1764              7.796600e+08                    1.515100e+07   
1765              6.100610e+08                    7.638600e+07   
1766              3.363190e+08                    2.542950e+08   
1767              1.518400e+08                    1.440900e+07   

      2023 Common Stock Equity  2023 Total Capitalization  \
0                -5.202000e+09               2.406800e+10   
1                          NaN                        NaN   
2                 2.148690e+08               2.911020e+08   
3                 7.352240e+08               7.735520e+08   
4                 6.214600e+10               1.574270e+11   
...                        ...                        ...   
1763                       NaN                        NaN   
1764              7.961180e+08               7.961180e+08   
1765              7.251120e+08               1.859271e+09   
1766              4.073280e+08               4.073280e+08   
1767  

In [95]:
df_small.set_index("Ticker", inplace=True)
df_small

2023 Treasury Shares Number  2023 Ordinary Shares Number  \
Ticker                                                             
AAL                             0.0                 6.542732e+08   
AAME                            NaN                          NaN   
AAOI                            NaN                 3.814800e+07   
AAON                            NaN                 8.150838e+07   
AAPL                            0.0                 1.555006e+10   
...                             ...                          ...   
ZKIN                            NaN                          NaN   
ZLAB                      4912200.0                 9.722391e+08   
ZS                              NaN                 1.471690e+08   
ZUMZ                            NaN                 1.948900e+07   
true                            NaN                 9.109154e+07   

        2023 Share Issued  2023 Net Debt  2023 Total Debt  \
Ticker                                                      
AAL          6.542732e+08   3.232400e+10     4.066300e+10   
AAME                  NaN            NaN              NaN   
AAOI         3.814800e+07   6.983200e+07     1.210730e+08   
AAON         8.150838e+07   3.804100e+07     5.055000e+07   
AAPL         1.555006e+10   8.112300e+10     1.110880e+11   
...                   ...            ...              ...   
ZKIN                  NaN            NaN              NaN   
ZLAB         9.771513e+08            NaN     1.515100e+07   
ZS           1.471690e+08            NaN     1.210545e+09   
ZUMZ         1.948900e+07            NaN     2.542950e+08   
true         9.109154e+07            NaN     1.440900e+07   

        2023 Tangible Book Value  2023 Invested Capital  2023 Working Capital  \
Ticker                                                                          
AAL                -1.134400e+10           2.770000e+10         -8.490000e+09   
AAME                         NaN                    NaN                   NaN   
AAOI                2.062110e+08           3.300670e+08          7.924700e+07   
AAON                5.852790e+08           7.735520e+08          2.822050e+08   
AAPL                6.214600e+10           1.732340e+11         -1.742000e+09   
...                          ...                    ...                   ...   
ZKIN                         NaN                    NaN                   NaN   
ZLAB                7.796600e+08           7.961180e+08          7.365390e+08   
ZS                  6.100610e+08           1.859271e+09          1.354446e+09   
ZUMZ                3.363190e+08           4.073280e+08          1.943690e+08   
true                1.518400e+08           1.602150e+08          1.341040e+08   

        2023 Net Tangible Assets  2023 Capital Lease Obligations  \
Ticker                                                             
AAL                -1.134400e+10                    7.761000e+09   
AAME                         NaN                             NaN   
AAOI                2.062110e+08                    5.875000e+06   
AAON                5.852790e+08                    1.222200e+07   
AAPL                6.214600e+10                             NaN   
...                          ...                             ...   
ZKIN                         NaN                             NaN   
ZLAB                7.796600e+08                    1.515100e+07   
ZS                  6.100610e+08                    7.638600e+07   
ZUMZ                3.363190e+08                    2.542950e+08   
true                1.518400e+08                    1.440900e+07   

        2023 Common Stock Equity  2023 Total Capitalization  \
Ticker                                                        
AAL                -5.202000e+09               2.406800e+10   
AAME                         NaN                        NaN   
AAOI                2.148690e+08               2.911020e+08   
AAON                7.352240e+08               7.735520e+08   
AAPL        

In [117]:
y = pd.read_csv("../raw_data/raw_data_target.csv")
y = y.drop(columns=["Unnamed: 0"])
y = y.set_index("Ticker")
y = y.dropna()
y

Ratio ticker sp500
Ticker                    
AAL               0.785045
AAOI              4.957467
AAON              0.974026
AAPL              0.860731
ABCB              1.232920
...                    ...
ZKIN              0.749892
ZLAB              0.487622
ZS                1.194828
ZUMZ              0.843950
true              0.962451

[1632 rows x 1 columns]

In [118]:
df_small_2023 = df_small.filter(like="2023", axis=1).copy()
df_small_2023

2023 Treasury Shares Number  2023 Ordinary Shares Number  \
Ticker                                                             
AAL                             0.0                 6.542732e+08   
AAME                            NaN                          NaN   
AAOI                            NaN                 3.814800e+07   
AAON                            NaN                 8.150838e+07   
AAPL                            0.0                 1.555006e+10   
...                             ...                          ...   
ZKIN                            NaN                          NaN   
ZLAB                      4912200.0                 9.722391e+08   
ZS                              NaN                 1.471690e+08   
ZUMZ                            NaN                 1.948900e+07   
true                            NaN                 9.109154e+07   

        2023 Share Issued  2023 Net Debt  2023 Total Debt  \
Ticker                                                      
AAL          6.542732e+08   3.232400e+10     4.066300e+10   
AAME                  NaN            NaN              NaN   
AAOI         3.814800e+07   6.983200e+07     1.210730e+08   
AAON         8.150838e+07   3.804100e+07     5.055000e+07   
AAPL         1.555006e+10   8.112300e+10     1.110880e+11   
...                   ...            ...              ...   
ZKIN                  NaN            NaN              NaN   
ZLAB         9.771513e+08            NaN     1.515100e+07   
ZS           1.471690e+08            NaN     1.210545e+09   
ZUMZ         1.948900e+07            NaN     2.542950e+08   
true         9.109154e+07            NaN     1.440900e+07   

        2023 Tangible Book Value  2023 Invested Capital  2023 Working Capital  \
Ticker                                                                          
AAL                -1.134400e+10           2.770000e+10         -8.490000e+09   
AAME                         NaN                    NaN                   NaN   
AAOI                2.062110e+08           3.300670e+08          7.924700e+07   
AAON                5.852790e+08           7.735520e+08          2.822050e+08   
AAPL                6.214600e+10           1.732340e+11         -1.742000e+09   
...                          ...                    ...                   ...   
ZKIN                         NaN                    NaN                   NaN   
ZLAB                7.796600e+08           7.961180e+08          7.365390e+08   
ZS                  6.100610e+08           1.859271e+09          1.354446e+09   
ZUMZ                3.363190e+08           4.073280e+08          1.943690e+08   
true                1.518400e+08           1.602150e+08          1.341040e+08   

        2023 Net Tangible Assets  2023 Capital Lease Obligations  \
Ticker                                                             
AAL                -1.134400e+10                    7.761000e+09   
AAME                         NaN                             NaN   
AAOI                2.062110e+08                    5.875000e+06   
AAON                5.852790e+08                    1.222200e+07   
AAPL                6.214600e+10                             NaN   
...                          ...                             ...   
ZKIN                         NaN                             NaN   
ZLAB                7.796600e+08                    1.515100e+07   
ZS                  6.100610e+08                    7.638600e+07   
ZUMZ                3.363190e+08                    2.542950e+08   
true                1.518400e+08                    1.440900e+07   

        2023 Common Stock Equity  2023 Total Capitalization  \
Ticker                                                        
AAL                -5.202000e+09               2.406800e+10   
AAME                         NaN                        NaN   
AAOI                2.148690e+08               2.911020e+08   
AAON                7.352240e+08               7.735520e+08   
AAPL        

In [119]:
df_small_2023 = df_small_2023.reset_index()
df_small_2023

Ticker  2023 Treasury Shares Number  2023 Ordinary Shares Number  \
0       AAL                          0.0                 6.542732e+08   
1      AAME                          NaN                          NaN   
2      AAOI                          NaN                 3.814800e+07   
3      AAON                          NaN                 8.150838e+07   
4      AAPL                          0.0                 1.555006e+10   
...     ...                          ...                          ...   
1763   ZKIN                          NaN                          NaN   
1764   ZLAB                    4912200.0                 9.722391e+08   
1765     ZS                          NaN                 1.471690e+08   
1766   ZUMZ                          NaN                 1.948900e+07   
1767   true                          NaN                 9.109154e+07   

      2023 Share Issued  2023 Net Debt  2023 Total Debt  \
0          6.542732e+08   3.232400e+10     4.066300e+10   
1                   NaN            NaN              NaN   
2          3.814800e+07   6.983200e+07     1.210730e+08   
3          8.150838e+07   3.804100e+07     5.055000e+07   
4          1.555006e+10   8.112300e+10     1.110880e+11   
...                 ...            ...              ...   
1763                NaN            NaN              NaN   
1764       9.771513e+08            NaN     1.515100e+07   
1765       1.471690e+08            NaN     1.210545e+09   
1766       1.948900e+07            NaN     2.542950e+08   
1767       9.109154e+07            NaN     1.440900e+07   

      2023 Tangible Book Value  2023 Invested Capital  2023 Working Capital  \
0                -1.134400e+10           2.770000e+10         -8.490000e+09   
1                          NaN                    NaN                   NaN   
2                 2.062110e+08           3.300670e+08          7.924700e+07   
3                 5.852790e+08           7.735520e+08          2.822050e+08   
4                 6.214600e+10           1.732340e+11         -1.742000e+09   
...                        ...                    ...                   ...   
1763                       NaN                    NaN                   NaN   
1764              7.796600e+08           7.961180e+08          7.365390e+08   
1765              6.100610e+08           1.859271e+09          1.354446e+09   
1766              3.363190e+08           4.073280e+08          1.943690e+08   
1767              1.518400e+08           1.602150e+08          1.341040e+08   

      2023 Net Tangible Assets  2023 Capital Lease Obligations  \
0                -1.134400e+10                    7.761000e+09   
1                          NaN                             NaN   
2                 2.062110e+08                    5.875000e+06   
3                 5.852790e+08                    1.222200e+07   
4                 6.214600e+10                             NaN   
...                        ...                             ...   
1763                       NaN                             NaN   
1764              7.796600e+08                    1.515100e+07   
1765              6.100610e+08                    7.638600e+07   
1766              3.363190e+08                    2.542950e+08   
1767              1.518400e+08                    1.440900e+07   

      2023 Common Stock Equity  2023 Total Capitalization  \
0                -5.202000e+09               2.406800e+10   
1                          NaN                        NaN   
2                 2.148690e+08               2.911020e+08   
3                 7.352240e+08               7.735520e+08   
4                 6.214600e+10               1.574270e+11   
...                        ...                        ...   
1763                       NaN                        NaN   
1764              7.961180e+08               7.961180e+08   
1765              7.251120e+08               1.859271e+09   
1766              4.073280e+08               4.073280e+08   
1767  

In [120]:
df_small_2023_clean = clean_dataframe(df_small_2023)
df_small_2023_clean = preprocessing_the_data(df_small_2023_clean)


In [121]:
df_small_2023_clean

pipeline__2023 Ordinary Shares Number  pipeline__2023 Share Issued  \
0                                  7.731698                     7.186123   
1                                 -0.000013                    -0.046663   
2                                  0.544114                     0.462351   
3                                194.657860                   182.050004   
4                                  0.387816                     0.356790   
...                                     ...                          ...   
1614                               1.380432                     1.244703   
1615                              11.721829                    10.976437   
1616                               1.368084                     1.233151   
1617                              -0.234163                    -0.265703   
1618                               0.664372                     0.574850   

      pipeline__2023 Total Debt  pipeline__2023 Tangible Book Value  \
0                     53.789215                          -21.547412   
1                     -0.023633                            0.124669   
2                     -0.117241                            0.835928   
3                    147.267007                          116.344543   
4                      0.665027                            4.096762   
...                         ...                                 ...   
1614                   2.559270                            7.603349   
1615                  -0.164228                            1.200652   
1616                   1.422465                            0.882427   
1617                   0.153197                            0.368795   
1618                  -0.165212                            0.022650   

      pipeline__2023 Invested Capital  pipeline__2023 Working Capital  \
0                           14.442738                      -26.659280   
1                           -0.095568                        0.065208   
2                            0.140001                        0.698163   
3                           91.747201                       -5.614625   
4                            1.889221                       -0.181936   
...                               ...                             ...   
1614                         3.614143                       -0.181936   
1615                         0.151988                        2.115072   
1616                         0.716711                        4.042108   
1617                        -0.054529                        0.424233   
1618                        -0.185790                        0.236288   

      pipeline__2023 Net Tangible Assets  \
0                             -21.511108   
1                               0.124457   
2                               0.834518   
3                             116.148510   
4                               4.089857   
...                                  ...   
1614                            8.414733   
1615                            1.198627   
1616                            0.880939   
1617                            0.368172   
1618                            0.022610   

      pipeline__2023 Capital Lease Obligations  \
0                                   130.236102   
1                                    -0.059291   
2                                     0.047346   
3                                    -0.157998   
4                                    -0.157998   
...                                        ...   
1614                                 -0.090794   
1615                                  0.096556   
1616                                  1.125378   
1617                                  4.114462   
1618                                  0.084090   

      pipeline__2023 Common Stock Equity  pipeline__2023 Total Capitalization  \
0                              -5.195071                            13.104134   
1                              -0.072111                            -0.

In [122]:
df_small_2023_clean = df_small_2023_clean.set_index("Ticker")
df_small_2023_clean

pipeline__2023 Ordinary Shares Number  pipeline__2023 Share Issued  \
Ticker                                                                       
AAL                                  7.731698                     7.186123   
AAOI                                -0.000013                    -0.046663   
AAON                                 0.544114                     0.462351   
AAPL                               194.657860                   182.050004   
ABCB                                 0.387816                     0.356790   
...                                       ...                          ...   
ZION                                 1.380432                     1.244703   
ZLAB                                11.721829                    10.976437   
ZS                                   1.368084                     1.233151   
ZUMZ                                -0.234163                    -0.265703   
true                                 0.664372                     0.574850   

        pipeline__2023 Total Debt  pipeline__2023 Tangible Book Value  \
Ticker                                                                  
AAL                     53.789215                          -21.547412   
AAOI                    -0.023633                            0.124669   
AAON                    -0.117241                            0.835928   
AAPL                   147.267007                          116.344543   
ABCB                     0.665027                            4.096762   
...                           ...                                 ...   
ZION                     2.559270                            7.603349   
ZLAB                    -0.164228                            1.200652   
ZS                       1.422465                            0.882427   
ZUMZ                     0.153197                            0.368795   
true                    -0.165212                            0.022650   

        pipeline__2023 Invested Capital  pipeline__2023 Working Capital  \
Ticker                                                                    
AAL                           14.442738                      -26.659280   
AAOI                          -0.095568                        0.065208   
AAON                           0.140001                        0.698163   
AAPL                          91.747201                       -5.614625   
ABCB                           1.889221                       -0.181936   
...                                 ...                             ...   
ZION                           3.614143                       -0.181936   
ZLAB                           0.151988                        2.115072   
ZS                             0.716711                        4.042108   
ZUMZ                          -0.054529                        0.424233   
true                          -0.185790                        0.236288   

        pipeline__2023 Net Tangible Assets  \
Ticker                                       
AAL                             -21.511108   
AAOI                              0.124457   
AAON                              0.834518   
AAPL                            116.148510   
ABCB                              4.089857   
...                                    ...   
ZION                              8.414733   
ZLAB                              1.198627   
ZS                                0.880939   
ZUMZ                              0.368172   
true                              0.022610   

        pipeline__2023 Capital Lease Obligations  \
Ticker                                             
AAL                                   130.236102   
AAOI                                   -0.059291   
AAON                                    0.047346   
AAPL                                   -0.157998   
ABCB                                   -0.157998   
...                                          ...   
ZION                                   -0.090794   


In [126]:
df = df_small_2023_clean.join( y, how="inner")
df
                    

pipeline__2023 Ordinary Shares Number  pipeline__2023 Share Issued  \
Ticker                                                                       
AAL                                  7.731698                     7.186123   
AAOI                                -0.000013                    -0.046663   
AAON                                 0.544114                     0.462351   
AAPL                               194.657860                   182.050004   
ABCB                                 0.387816                     0.356790   
...                                       ...                          ...   
ZION                                 1.380432                     1.244703   
ZLAB                                11.721829                    10.976437   
ZS                                   1.368084                     1.233151   
ZUMZ                                -0.234163                    -0.265703   
true                                 0.664372                     0.574850   

        pipeline__2023 Total Debt  pipeline__2023 Tangible Book Value  \
Ticker                                                                  
AAL                     53.789215                          -21.547412   
AAOI                    -0.023633                            0.124669   
AAON                    -0.117241                            0.835928   
AAPL                   147.267007                          116.344543   
ABCB                     0.665027                            4.096762   
...                           ...                                 ...   
ZION                     2.559270                            7.603349   
ZLAB                    -0.164228                            1.200652   
ZS                       1.422465                            0.882427   
ZUMZ                     0.153197                            0.368795   
true                    -0.165212                            0.022650   

        pipeline__2023 Invested Capital  pipeline__2023 Working Capital  \
Ticker                                                                    
AAL                           14.442738                      -26.659280   
AAOI                          -0.095568                        0.065208   
AAON                           0.140001                        0.698163   
AAPL                          91.747201                       -5.614625   
ABCB                           1.889221                       -0.181936   
...                                 ...                             ...   
ZION                           3.614143                       -0.181936   
ZLAB                           0.151988                        2.115072   
ZS                             0.716711                        4.042108   
ZUMZ                          -0.054529                        0.424233   
true                          -0.185790                        0.236288   

        pipeline__2023 Net Tangible Assets  \
Ticker                                       
AAL                             -21.511108   
AAOI                              0.124457   
AAON                              0.834518   
AAPL                            116.148510   
ABCB                              4.089857   
...                                    ...   
ZION                              8.414733   
ZLAB                              1.198627   
ZS                                0.880939   
ZUMZ                              0.368172   
true                              0.022610   

        pipeline__2023 Capital Lease Obligations  \
Ticker                                             
AAL                                   130.236102   
AAOI                                   -0.059291   
AAON                                    0.047346   
AAPL                                   -0.157998   
ABCB                                   -0.157998   
...                                          ...   
ZION                                   -0.090794   


In [132]:
df = df.dropna()

In [133]:
df.isna().sum()

pipeline__2023 Ordinary Shares Number                   0
pipeline__2023 Share Issued                             0
pipeline__2023 Total Debt                               0
pipeline__2023 Tangible Book Value                      0
pipeline__2023 Invested Capital                         0
                                                       ..
pipeline__2023 Operating Gains Losses                   0
pipeline__2023 Net Income From Continuing Operations    0
pipeline__2023 Change In Payable                        0
pipeline__2023 Change In Account Payable                0
Ratio ticker sp500                                      0
Length: 103, dtype: int64

In [134]:
X = df.drop(columns=["Ratio ticker sp500"])
y = df["Ratio ticker sp500"]

In [135]:
y.isna().sum()

0

In [136]:
X_train, X_test, y_train, y_test = train_test_split(X, y, test_size=0.3)
X_test, X_val, y_test, y_val = train_test_split(X_test, y_test, test_size = 0.5)

In [137]:
xgb_reg = XGBRegressor(max_depth=10, n_estimators=100, learning_rate=0.1)

xgb_reg.fit(X_train, y_train,
    # evaluate loss at each iteration
    eval_set=[(X_train, y_train), (X_val, y_val)],  
    # stop iterating when eval loss increases 5 times in a row
    early_stopping_rounds=5)


#y_pred = xgb_reg.predict(X_test)
 

#Or integrate it into scikit-learn as a Pipeline 🎉

#from sklearn.pipeline import make_pipeline

#pipe_xgb = make_pipeline(xgb_reg)
cv_results = cross_validate(xgb_reg, X_train, y_train, cv=10, scoring='r2')
cv_results

[0]	validation_0-rmse:0.58054	validation_1-rmse:0.75832
[1]	validation_0-rmse:0.54345	validation_1-rmse:0.74128
[2]	validation_0-rmse:0.50901	validation_1-rmse:0.73315
[3]	validation_0-rmse:0.47758	validation_1-rmse:0.72789
[4]	validation_0-rmse:0.44841	validation_1-rmse:0.72371
[5]	validation_0-rmse:0.42198	validation_1-rmse:0.71813
[6]	validation_0-rmse:0.39670	validation_1-rmse:0.71246
[7]	validation_0-rmse:0.37372	validation_1-rmse:0.71105
[8]	validation_0-rmse:0.35290	validation_1-rmse:0.70702
[9]	validation_0-rmse:0.33357	validation_1-rmse:0.70327
[10]	validation_0-rmse:0.31501	validation_1-rmse:0.70172
[11]	validation_0-rmse:0.29809	validation_1-rmse:0.69934


/Users/manonantonacci/.pyenv/versions/3.10.6/envs/project_env/lib/python3.10/site-packages/xgboost/sklearn.py:889: UserWarning: `early_stopping_rounds` in `fit` method is deprecated for better compatibility with scikit-learn, use `early_stopping_rounds` in constructor or`set_params` instead.
  warnings.warn(


[12]	validation_0-rmse:0.28211	validation_1-rmse:0.69621
[13]	validation_0-rmse:0.26750	validation_1-rmse:0.69486
[14]	validation_0-rmse:0.25442	validation_1-rmse:0.69211
[15]	validation_0-rmse:0.24212	validation_1-rmse:0.69010
[16]	validation_0-rmse:0.23027	validation_1-rmse:0.68765
[17]	validation_0-rmse:0.21864	validation_1-rmse:0.68411
[18]	validation_0-rmse:0.20855	validation_1-rmse:0.68116
[19]	validation_0-rmse:0.19781	validation_1-rmse:0.67906
[20]	validation_0-rmse:0.18863	validation_1-rmse:0.67760
[21]	validation_0-rmse:0.17949	validation_1-rmse:0.67480
[22]	validation_0-rmse:0.17136	validation_1-rmse:0.67395
[23]	validation_0-rmse:0.16356	validation_1-rmse:0.67272
[24]	validation_0-rmse:0.15615	validation_1-rmse:0.67144
[25]	validation_0-rmse:0.14950	validation_1-rmse:0.67059
[26]	validation_0-rmse:0.14218	validation_1-rmse:0.66936
[27]	validation_0-rmse:0.13523	validation_1-rmse:0.66924
[28]	validation_0-rmse:0.12944	validation_1-rmse:0.66799
[29]	validation_0-rmse:0.12451	

{'fit_time': array([1.20113921, 1.21873498, 1.394068  , 1.33684778, 1.33379102,
        1.39492202, 1.36335373, 1.233639  , 1.23389292, 1.23844504]),
 'score_time': array([0.00544786, 0.00527   , 0.00490904, 0.00587916, 0.00502396,
        0.01026583, 0.00485301, 0.00483012, 0.00509501, 0.00492406]),
 'test_score': array([-0.06268463, -1.24007221,  0.30536944,  0.31781825, -3.03564146,
         0.25497374,  0.1747977 ,  0.34439127,  0.147849  ,  0.03464388])}

In [138]:
cv_results = cross_validate(xgb_reg, X_train, y_train, cv=10, scoring='r2')
cv_results

{'fit_time': array([1.23087597, 1.1713419 , 1.217345  , 1.30810595, 1.20722318,
        1.21895909, 1.30006409, 1.17635989, 1.18155193, 1.18564773]),
 'score_time': array([0.00507212, 0.00501609, 0.00485706, 0.0050621 , 0.00489283,
        0.00531793, 0.00486112, 0.00489807, 0.00486588, 0.00547314]),
 'test_score': array([-0.06268463, -1.24007221,  0.30536944,  0.31781825, -3.03564146,
         0.25497374,  0.1747977 ,  0.34439127,  0.147849  ,  0.03464388])}

# Trying Classification

In [140]:
y = pd.read_csv("../raw_data/raw_data_target.csv")
y = y.drop(columns=["Unnamed: 0"])
y = y.set_index("Ticker")
y = y.dropna()
y

Ratio ticker sp500
Ticker                    
AAL               0.785045
AAOI              4.957467
AAON              0.974026
AAPL              0.860731
ABCB              1.232920
...                    ...
ZKIN              0.749892
ZLAB              0.487622
ZS                1.194828
ZUMZ              0.843950
true              0.962451

[1632 rows x 1 columns]

## Binary classification just 2023 data

In [143]:
y["2024 Ratio as Class"] = y["Ratio ticker sp500"].apply(lambda x: 0 if x < 1 else 1)
y

Ratio ticker sp500  2024 Ratio as Class
Ticker                                         
AAL               0.785045                    0
AAOI              4.957467                    1
AAON              0.974026                    0
AAPL              0.860731                    0
ABCB              1.232920                    1
...                    ...                  ...
ZKIN              0.749892                    0
ZLAB              0.487622                    0
ZS                1.194828                    1
ZUMZ              0.843950                    0
true              0.962451                    0

[1632 rows x 2 columns]

In [147]:
df.drop(columns=["Ratio ticker sp500"], inplace=True)
df

/var/folders/0c/m7z5hx0x5hlbkb63dy8xn9tr0000gn/T/ipykernel_70180/754919074.py:1: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df.drop(columns=["Ratio ticker sp500"], inplace=True)


pipeline__2023 Ordinary Shares Number  pipeline__2023 Share Issued  \
Ticker                                                                       
AAL                                  7.731698                     7.186123   
AAOI                                -0.000013                    -0.046663   
AAON                                 0.544114                     0.462351   
AAPL                               194.657860                   182.050004   
ABCB                                 0.387816                     0.356790   
...                                       ...                          ...   
ZION                                 1.380432                     1.244703   
ZLAB                                11.721829                    10.976437   
ZS                                   1.368084                     1.233151   
ZUMZ                                -0.234163                    -0.265703   
true                                 0.664372                     0.574850   

        pipeline__2023 Total Debt  pipeline__2023 Tangible Book Value  \
Ticker                                                                  
AAL                     53.789215                          -21.547412   
AAOI                    -0.023633                            0.124669   
AAON                    -0.117241                            0.835928   
AAPL                   147.267007                          116.344543   
ABCB                     0.665027                            4.096762   
...                           ...                                 ...   
ZION                     2.559270                            7.603349   
ZLAB                    -0.164228                            1.200652   
ZS                       1.422465                            0.882427   
ZUMZ                     0.153197                            0.368795   
true                    -0.165212                            0.022650   

        pipeline__2023 Invested Capital  pipeline__2023 Working Capital  \
Ticker                                                                    
AAL                           14.442738                      -26.659280   
AAOI                          -0.095568                        0.065208   
AAON                           0.140001                        0.698163   
AAPL                          91.747201                       -5.614625   
ABCB                           1.889221                       -0.181936   
...                                 ...                             ...   
ZION                           3.614143                       -0.181936   
ZLAB                           0.151988                        2.115072   
ZS                             0.716711                        4.042108   
ZUMZ                          -0.054529                        0.424233   
true                          -0.185790                        0.236288   

        pipeline__2023 Net Tangible Assets  \
Ticker                                       
AAL                             -21.511108   
AAOI                              0.124457   
AAON                              0.834518   
AAPL                            116.148510   
ABCB                              4.089857   
...                                    ...   
ZION                              8.414733   
ZLAB                              1.198627   
ZS                                0.880939   
ZUMZ                              0.368172   
true                              0.022610   

        pipeline__2023 Capital Lease Obligations  \
Ticker                                             
AAL                                   130.236102   
AAOI                                   -0.059291   
AAON                                    0.047346   
AAPL                                   -0.157998   
ABCB                                   -0.157998   
...                                          ...   
ZION                                   -0.090794   


In [149]:
y = y.drop(columns=["Ratio ticker sp500"])
y

2024 Ratio as Class
Ticker                     
AAL                       0
AAOI                      1
AAON                      0
AAPL                      0
ABCB                      1
...                     ...
ZKIN                      0
ZLAB                      0
ZS                        1
ZUMZ                      0
true                      0

[1632 rows x 1 columns]

In [150]:

df = df.join(y, how="left")
df.isna().sum()

pipeline__2023 Ordinary Shares Number                   0
pipeline__2023 Share Issued                             0
pipeline__2023 Total Debt                               0
pipeline__2023 Tangible Book Value                      0
pipeline__2023 Invested Capital                         0
                                                       ..
pipeline__2023 Operating Gains Losses                   0
pipeline__2023 Net Income From Continuing Operations    0
pipeline__2023 Change In Payable                        0
pipeline__2023 Change In Account Payable                0
2024 Ratio as Class                                     0
Length: 103, dtype: int64

In [151]:
X = df.drop(columns=["2024 Ratio as Class"])
y = df["2024 Ratio as Class"]

In [152]:
X_train, X_test, y_train, y_test = train_test_split(X, y, test_size=0.3)
X_test, X_val, y_test, y_val = train_test_split(X_test, y_test, test_size = 0.5)

In [153]:
xgb_reg = XGBRegressor(max_depth=10, n_estimators=100, learning_rate=0.1)

xgb_reg.fit(X_train, y_train,
    # evaluate loss at each iteration
    eval_set=[(X_train, y_train), (X_val, y_val)],  
    # stop iterating when eval loss increases 5 times in a row
    early_stopping_rounds=5)


#y_pred = xgb_reg.predict(X_test)
 

#Or integrate it into scikit-learn as a Pipeline 🎉

#from sklearn.pipeline import make_pipeline

#pipe_xgb = make_pipeline(xgb_reg)
cv_results = cross_validate(xgb_reg, X_train, y_train, cv=10, scoring='r2')
cv_results

[0]	validation_0-rmse:0.42309	validation_1-rmse:0.46431
[1]	validation_0-rmse:0.38817	validation_1-rmse:0.46010
[2]	validation_0-rmse:0.36041	validation_1-rmse:0.45836
[3]	validation_0-rmse:0.33427	validation_1-rmse:0.45744
[4]	validation_0-rmse:0.31107	validation_1-rmse:0.45839
[5]	validation_0-rmse:0.28757	validation_1-rmse:0.46117
[6]	validation_0-rmse:0.26442	validation_1-rmse:0.46522
[7]	validation_0-rmse:0.24779	validation_1-rmse:0.46642
[8]	validation_0-rmse:0.22863	validation_1-rmse:0.46733


/Users/manonantonacci/.pyenv/versions/3.10.6/envs/project_env/lib/python3.10/site-packages/xgboost/sklearn.py:889: UserWarning: `early_stopping_rounds` in `fit` method is deprecated for better compatibility with scikit-learn, use `early_stopping_rounds` in constructor or`set_params` instead.
  warnings.warn(


{'fit_time': array([1.49246502, 1.53010321, 1.39793301, 1.46671391, 1.42430305,
        1.38630104, 1.46446586, 1.41349983, 1.49846411, 1.35320902]),
 'score_time': array([0.00599408, 0.00564575, 0.00505495, 0.00512099, 0.00552082,
        0.00504589, 0.00495791, 0.00487399, 0.00492692, 0.00484896]),
 'test_score': array([-0.16231561,  0.14546394,  0.06921977,  0.00467288, -0.07564354,
        -0.0888356 ,  0.09593487, -0.15380442,  0.04947305, -0.10452294])}

## binary classification ratios

In [155]:
X_small_reduced

pipeline__2023 Ratio ticker sp500  pipeline__2022 Ratio ticker sp500  \
Ticker                                                                         
AAL                              0.110173                          -0.090977   
AAOI                            17.045832                          -0.781155   
AAON                             0.937091                           0.512387   
AAPL                             0.587249                           0.474382   
ABCB                             0.279406                           0.407539   
...                                   ...                                ...   
ZKIN                            -1.900304                          -0.962432   
ZLAB                            -0.289921                          -0.519939   
ZS                               0.316123                          -0.377801   
ZUMZ                            -0.408094                          -0.032692   
true                             0.532747                           0.024220   

        pipeline__2021 Ratio ticker sp500  pipeline__2020 Ratio ticker sp500  
Ticker                                                                        
AAL                             -0.006855                          -0.747803  
AAOI                            -0.905159                          -0.533057  
AAON                             0.063391                           0.508978  
AAPL                             0.061296                           1.720461  
ABCB                             0.190881                          -0.168701  
...                                   ...                                ...  
ZKIN                             1.593082                           0.020274  
ZLAB                            -1.058512                           3.386363  
ZS                               0.826357                           0.922797  
ZUMZ                             0.374460                           0.281814  
true                            -0.608170                          -0.251870  

[1632 rows x 4 columns]

In [157]:
y = pd.read_csv("../raw_data/raw_data_target.csv")
y = y.drop(columns=["Unnamed: 0"])
y = y.set_index("Ticker")
y = y.dropna()
y

Ratio ticker sp500
Ticker                    
AAL               0.785045
AAOI              4.957467
AAON              0.974026
AAPL              0.860731
ABCB              1.232920
...                    ...
ZKIN              0.749892
ZLAB              0.487622
ZS                1.194828
ZUMZ              0.843950
true              0.962451

[1632 rows x 1 columns]

In [158]:
y["2024 Ratio as Class"] = y["Ratio ticker sp500"].apply(lambda x: 0 if x < 1 else 1)
y

Ratio ticker sp500  2024 Ratio as Class
Ticker                                         
AAL               0.785045                    0
AAOI              4.957467                    1
AAON              0.974026                    0
AAPL              0.860731                    0
ABCB              1.232920                    1
...                    ...                  ...
ZKIN              0.749892                    0
ZLAB              0.487622                    0
ZS                1.194828                    1
ZUMZ              0.843950                    0
true              0.962451                    0

[1632 rows x 2 columns]

In [159]:
y = y.drop(columns=["Ratio ticker sp500"])
y

2024 Ratio as Class
Ticker                     
AAL                       0
AAOI                      1
AAON                      0
AAPL                      0
ABCB                      1
...                     ...
ZKIN                      0
ZLAB                      0
ZS                        1
ZUMZ                      0
true                      0

[1632 rows x 1 columns]

In [160]:
X_train, X_test, y_train, y_test = train_test_split(X_small_reduced, y, test_size=0.3)
X_test, X_val, y_test, y_val = train_test_split(X_test, y_test, test_size = 0.5)

In [162]:
xgb_reg = XGBRegressor(max_depth=10, n_estimators=100, learning_rate=0.1)

xgb_reg.fit(X_train, y_train,
    # evaluate loss at each iteration
    eval_set=[(X_train, y_train), (X_val, y_val)],  
    # stop iterating when eval loss increases 5 times in a row
    early_stopping_rounds=5)


#y_pred = xgb_reg.predict(X_test)
 

#Or integrate it into scikit-learn as a Pipeline 🎉

#from sklearn.pipeline import make_pipeline

#pipe_xgb = make_pipeline(xgb_reg)
cv_results = cross_validate(xgb_reg, X_train, y_train, cv=5, scoring='r2')
cv_results

[0]	validation_0-rmse:0.42892	validation_1-rmse:0.44826
[1]	validation_0-rmse:0.40143	validation_1-rmse:0.44267
[2]	validation_0-rmse:0.37802	validation_1-rmse:0.44000
[3]	validation_0-rmse:0.35648	validation_1-rmse:0.44382
[4]	validation_0-rmse:0.33877	validation_1-rmse:0.44435
[5]	validation_0-rmse:0.32199	validation_1-rmse:0.44248
[6]	validation_0-rmse:0.30716	validation_1-rmse:0.44242
[7]	validation_0-rmse:0.29231	validation_1-rmse:0.44370


/Users/manonantonacci/.pyenv/versions/3.10.6/envs/project_env/lib/python3.10/site-packages/xgboost/sklearn.py:889: UserWarning: `early_stopping_rounds` in `fit` method is deprecated for better compatibility with scikit-learn, use `early_stopping_rounds` in constructor or`set_params` instead.
  warnings.warn(


{'fit_time': array([0.13431001, 0.13204312, 0.11530495, 0.11377311, 0.10951614]),
 'score_time': array([0.002074  , 0.00154495, 0.00222421, 0.00222802, 0.00160289]),
 'test_score': array([ 0.07779139, -0.08003783, -0.00981855, -0.01330829,  0.04383725])}

In [163]:
data = pd.read_csv("../raw_data/raw_data_FINAL_ALL.csv")
data

Ticker  2023 Ordinary Shares Number  2023 Share Issued  2023 Net Debt  \
0         A                  292123241.0        292123241.0   1.145000e+09   
1        AA                  178472464.0        178472464.0   8.670000e+08   
2      AACG                   64000260.0         64585618.0            NaN   
3      AACI                    8072849.0          8072849.0   2.504155e+06   
4     AACIW                    8072849.0          8072849.0   2.504155e+06   
...     ...                          ...                ...            ...   
6329   ZVIA                   54220017.0         54220017.0            NaN   
6330   ZVRA                          NaN                NaN            NaN   
6331   ZVSA                     405205.0           405211.0            NaN   
6332   ZYME                   70115997.0         70115997.0            NaN   
6333   ZYXI                   32933776.0         41478820.0   1.302600e+07   

      2023 Total Debt  2023 Tangible Book Value  2023 Invested Capital  \
0        2.735000e+09              1.410000e+09           8.580000e+09   
1        1.915000e+09              4.068000e+09           6.062000e+09   
2        2.260687e+07             -1.421377e+08           1.130379e+08   
3        2.564439e+06              1.683079e+07           1.939523e+07   
4        2.564439e+06              1.683079e+07           1.939523e+07   
...               ...                       ...                    ...   
6329     1.948000e+06              8.635500e+07           8.987800e+07   
6330              NaN                       NaN                    NaN   
6331     8.656000e+03             -7.573306e+06           1.107460e+07   
6332     2.672200e+07              4.275060e+08           4.648060e+08   
6333     7.616800e+07              1.757000e+07           1.037340e+08   

      2023 Working Capital  2023 Net Tangible Assets  \
0             2.583000e+09              1.410000e+09   
1             1.375000e+09              4.068000e+09   
2            -2.439576e+08             -1.421377e+08   
3            -8.493234e+06              1.683079e+07   
4            -8.493234e+06              1.683079e+07   
...                    ...                       ...   
6329          5.497000e+07              8.635500e+07   
6330                   NaN                       NaN   
6331         -6.841639e+06             -7.573305e+06   
6332          3.571630e+08              4.275060e+08   
6333          6.932300e+07              1.757000e+07   

      2023 Common Stock Equity  2023 Total Capitalization  \
0                 5.845000e+09               8.580000e+09   
1                 4.251000e+09               5.983000e+09   
2                 1.130379e+08               1.130379e+08   
3                 1.683079e+07               1.683079e+07   
4                 1.683079e+07               1.683079e+07   
...                        ...                        ...   
6329              8.987800e+07               8.987800e+07   
6330                       NaN                        NaN   
6331              1.107460e+07               1.107460e+07   
6332              4.648060e+08               4.648060e+08   
6333              4.612900e+07               1.037340e+08   

      2023 Total Equity Gross Minority Interest  2023 Minority Interest  \
0                                  5.845000e+09                     NaN   
1                                  5.845000e+09            1.594000e+09   
2                                  1.129737e+08           -6.416100e+04   
3                                  1.683079e+07                     NaN   
4                                  1.683079e+07                     NaN   
...                                         ...                     ...   
6329                               6.176700e+07           -2.811100e+07   
6330                                        NaN                     NaN   
6331                               1.107460e+07                     NaN   
6332                   

In [170]:
#we have: Net Income, 

In [183]:
data.filter(like="Raw", axis=1).copy()

2023 Raw Materials  2022 Raw Materials  2021 Raw Materials  \
0            461000000.0        4.830000e+08         367000000.0   
1            930000000.0        1.108000e+09         794000000.0   
2                    NaN                 NaN                 NaN   
3                    NaN                 NaN                 NaN   
4                    NaN                 NaN                 NaN   
...                  ...                 ...                 ...   
6329           4714000.0        7.527000e+06          10193000.0   
6330                 NaN                 NaN                 NaN   
6331                 NaN                 NaN                 NaN   
6332                 NaN                 NaN                 NaN   
6333           4601000.0        3.506000e+06           4471000.0   

      2020 Raw Materials  2019 Raw Materials  2024 Raw Materials  
0            303000000.0                 NaN                 NaN  
1            553000000.0                 NaN                 NaN  
2                    NaN                 NaN                 NaN  
3                    NaN                 NaN                 NaN  
4                    NaN                 NaN                 NaN  
...                  ...                 ...                 ...  
6329           8155000.0                 NaN                 NaN  
6330                 NaN                 NaN                 NaN  
6331                 NaN                 NaN                 NaN  
6332                 NaN                 NaN                 NaN  
6333           3213000.0                 NaN                 NaN  

[6334 rows x 6 columns]

In [184]:
tickers_df = pd.read_csv("../raw_data/nasdaq_tickers_raw.csv")
tickers_df

Symbol                                               Name Last Sale  \
0         A             Agilent Technologies Inc. Common Stock   $145.48   
1        AA                    Alcoa Corporation Common Stock     $43.93   
2      AACG   ATA Creativity Global American Depositary Shares     $0.85   
3      AACI            Armada Acquisition Corp. I Common Stock  $11.3642   
4     AACIW                 Armada Acquisition Corp. I Warrant   $0.1707   
...     ...                                                ...       ...   
7128   ZVRA               Zevra Therapeutics Inc. Common Stock    $4.595   
7129   ZVSA             ZyVersa Therapeutics Inc. Common Stock   $4.2664   
7130    ZWS  Zurn Elkay Water Solutions Corporation Common ...    $30.46   
7131   ZYME                        Zymeworks Inc. Common Stock     $8.48   
7132   ZYXI                            Zynex Inc. Common Stock    $10.02   

      Net Change % Change    Market Cap        Country  IPO Year   Volume  \
0        -2.7300  -1.842%  4.263368e+10  United States    1999.0  1593543   
1         0.7300    1.69%  7.888057e+09  United States    2016.0  5272723   
2         0.0098   1.166%  2.720011e+07          China    2008.0    12048   
3        -0.0058  -0.051%  0.000000e+00  United States    2021.0     3672   
4         0.0108   6.754%  0.000000e+00  United States    2021.0    25825   
...          ...      ...           ...            ...       ...      ...   
7128      0.0350   0.768%  1.923168e+08  United States       NaN   271570   
7129      0.0128   0.301%  3.562000e+06  United States    2022.0    30162   
7130     -0.8300  -2.653%  5.260346e+09  United States    2012.0   820408   
7131     -0.2300  -2.641%  5.995775e+08  United States       NaN   555490   
7132     -0.0900   -0.89%  3.183873e+08  United States       NaN   122156   

           Sector                                           Industry  
0     Industrials                                Electrical Products  
1     Industrials                                           Aluminum  
2     Real Estate                            Other Consumer Services  
3         Finance                                       Blank Checks  
4         Finance                                       Blank Checks  
...           ...                                                ...  
7128  Health Care         Biotechnology: Pharmaceutical Preparations  
7129  Health Care         Biotechnology: Pharmaceutical Preparations  
7130  Industrials                    Industrial Machinery/Components  
7131  Health Care         Biotechnology: Pharmaceutical Preparations  
7132  Health Care  Biotechnology: Electromedical & Electrotherape...  

[7133 rows x 11 columns]